In [30]:
import os
from google.cloud import storage
from google.oauth2 import service_account
import pandas as pd
from sqlalchemy.engine import create_engine
#from datasets import load_dataset
from openai import OpenAI
import io
import base64
import random
import requests
from PIL import Image
import os
import pandas as pd
from sqlalchemy.engine import create_engine
import platform
import yaml
import json
import sys
from IPython.display import display,clear_output

In [16]:
gcp_cred='/Users/bineshkumar/Documents/gcp-cred.json'
cnfig_file="D:/config.yaml"
def get_from_cnfg(key_path,file_path=cnfig_file):
    try:
        with open(file_path, 'r') as file:
            data = yaml.safe_load(file)

        keys = key_path.split('.')
        value = data
        for key in keys:
            value = value[key]
        return value

    except FileNotFoundError:
        print(f"File {file_path} not found")
    except yaml.YAMLError as e:
        print(f"YAML parsing error: {e}")
    except KeyError:
        print(f"Key path {key_path} not found")
    except Exception as e:
        print(f"Error: {e}")
    return None
os_name = platform.system()

In [25]:
if 'google.colab' in sys.modules:
    from google.colab import drive
    drive.mount('/content/drive')
    from google.colab import userdata
    engine = create_engine(userdata.get('DB_URL'))
    gem_key=userdata.get('DB_URL')
    oai_key=userdata.get('DB_URL')
    source_folder='/content/drive/MyDrive/Health_Data/MIMIC_JPG_AVL/mimic-cxr-jpg/2.1.0/files/'
elif os_name == "Darwin":
    cnfig_file="/Users/bineshkumar/Documents/config.yaml"
    DB_URL = get_from_cnfg("cd_url",cnfig_file)
    gem_key=get_from_cnfg("gem_token",cnfig_file)
    oai_key=get_from_cnfg("oai_token",cnfig_file)
    ds_key=get_from_cnfg("ds_token",cnfig_file)
    claw_key=get_from_cnfg("claw_token",cnfig_file)
    source_folder='/Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files'
elif os_name == "Linux":
    DB_URL = get_from_cnfg("cd_url",cnfig_file)
    gem_key=get_from_cnfg("gem_token",cnfig_file)
    oai_key=get_from_cnfg("oai_token",cnfig_file)
    claw_key=get_from_cnfg("claw_token",cnfig_file)
    source_folder=""
else:
    cnfig_file="D:/config.yaml"
    DB_URL = get_from_cnfg("cd_url",cnfig_file)
    gem_key=get_from_cnfg("gem_token",cnfig_file)
    oai_key=get_from_cnfg("oai_token",cnfig_file)
    claw_key=get_from_cnfg("claw_token",cnfig_file)

engine = create_engine(DB_URL)

In [18]:
def fetch_generation_data(engine):
    import pandas as pd
    import re
    from sqlalchemy import text
    from sqlalchemy.dialects.postgresql.base import PGDialect
    def fake_get_server_version_info(self, connection):
        version_str = connection.execute(text("SELECT version()")).scalar()
        match = re.search(r'v(\d+)\.(\d+)\.(\d+)', version_str)
        if match:
            return tuple(map(int, match.groups()))
        return (13, 0, 0)
    PGDialect._get_server_version_info = fake_get_server_version_info
    query = f"SELECT id,question_id,condition as question_type, text as question,answer as ground_truth,image from mimic_all_qns; "
    return pd.read_sql(query, con=engine)



In [35]:
def download_file_from_gcs_if_needed(source_folder, file_link, service_account_json):
    local_file_path = source_folder + os.path.sep + file_link
    print(local_file_path)

    if os.path.exists(local_file_path):
        print(f"File already exists locally at {local_file_path}")
        return False

    print(f"File not found locally: {local_file_path}")
    gcs_bucket_name = "tbinvault"
    os.makedirs(os.path.dirname(local_file_path), exist_ok=True)
    if file_link.startswith("/"):
        gcs_blob_name = f"files{file_link}"
    else:
        gcs_blob_name = f"files/{file_link}"

    print(f"Attempting to download from gs://{gcs_bucket_name}/{gcs_blob_name}")

    credentials = service_account.Credentials.from_service_account_file(service_account_json)
    storage_client = storage.Client(credentials=credentials)
    bucket = storage_client.bucket(gcs_bucket_name)
    blob = bucket.blob(gcs_blob_name)

    try:
        blob.download_to_filename(local_file_path)
        print(f"Successfully downloaded to {local_file_path}")
        return True
    except Exception as e:
        print(f"Error downloading file: {e}")
        raise

In [36]:
for index, row in fetch_generation_data(engine).iterrows():
    download_file_from_gcs_if_needed(source_folder, row["image"], gcp_cred)


/Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p10/p10046166/s50051329/abea5eb9-b7c32823-3a14c5ca-77868030-69c83139.jpg
File already exists locally at /Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p10/p10046166/s50051329/abea5eb9-b7c32823-3a14c5ca-77868030-69c83139.jpg
/Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p10/p10046166/s50051329/abea5eb9-b7c32823-3a14c5ca-77868030-69c83139.jpg
File already exists locally at /Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p10/p10046166/s50051329/abea5eb9-b7c32823-3a14c5ca-77868030-69c83139.jpg
/Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p10/p10046166/s50051329/abea5eb9-b7c32823-3a14c5ca-77868030-69c83139.jpg
File already exists locally at /Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p10/p10046166/s50051329/abea5eb9-b7c32823-3a14c5ca-77868030-69c83139.jpg
/Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p10/p10046166/s50051329/abea5eb9-b7c32823-3a14c5ca-77868030-69c83139.jpg
File alread

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [11]:
download_file_from_gcs_if_needed('/Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files','p11/p11378150/s52705433/70e31905-dd605e80-305f056b-4f88ec80-cbb4b3fb.jpg',gcp_cred)

/Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p11/p11378150/s52705433/70e31905-dd605e80-305f056b-4f88ec80-cbb4b3fb.jpg
File not found locally: /Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p11/p11378150/s52705433/70e31905-dd605e80-305f056b-4f88ec80-cbb4b3fb.jpg
Attempting to download from gs://tbinvault/files/p11/p11378150/s52705433/70e31905-dd605e80-305f056b-4f88ec80-cbb4b3fb.jpg
Successfully downloaded to /Users/bineshkumar/Documents/mimic-cxr-jpg/2.1.0/files/p11/p11378150/s52705433/70e31905-dd605e80-305f056b-4f88ec80-cbb4b3fb.jpg


True

In [40]:
for index, row in fetch_generation_data(engine).iterrows():
    file_path = source_folder + os.path.sep +  row["image"]
    #print(f"File at {file_path}")
    if not os.path.exists(file_path):
        print(f"File does not exist  locally at {file_path}")